In [1]:
#libraries
import pandas as pd
import numpy as np

from lifelines.utils import concordance_index
from sklearn.model_selection import train_test_split

import helpers
import models
import classifiers
import graphing
import survival_models

2022-11-16 17:36:58.475810: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-11-16 17:37:00.056909: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2022-11-16 17:37:00.776027: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /sw/isaac/compilers/intel/oneAPI_2021.2.0/mpi/latest/libfabric/lib:/sw/isaac/compilers/intel/one

In [20]:
#code sources
import importlib
importlib.reload(helpers)
importlib.reload(models)
importlib.reload(classifiers)
importlib.reload(graphing)
importlib.reload(survival_models)

<module 'survival_models' from '/nfs/home/ababjac/dream-finrisk/scripts/survival_models.py'>

In [2]:
PATH = '/lustre/isaac/proj/UTK0196/dream-finrisk-data/DreamHF/'

In [3]:
#read training data
#taxonomy_train = pd.read_csv(PATH+'/train/taxtable.csv')
reads_train = pd.read_csv(PATH+'/train/readcounts_training.csv', index_col=0)
pheno_train = pd.read_csv(PATH+'/train/pheno_training.csv', index_col=0)

In [4]:
#read testing 
#taxonomy_test = pd.read_csv(PATH+'/test/taxtable.csv')
reads_test = pd.read_csv(PATH+'/test/readcounts_test.csv', index_col=0)
pheno_test = pd.read_csv(PATH+'/test/pheno_test.csv', index_col=0)

In [5]:
#preprocessing

reads_full = pd.concat([reads_train.T, reads_test.T])
pheno_full = pd.concat([pheno_train, pheno_test])

pheno_full.isnull().any()

Age                  False
BodyMassIndex         True
Smoking               True
BPTreatment          False
PrevalentDiabetes     True
PrevalentCHD          True
PrevalentHFAIL        True
Event                 True
Event_time            True
SystolicBP            True
NonHDLcholesterol     True
Sex                  False
dtype: bool

In [6]:
#correcting NA pheno

pheno_full = pheno_full.dropna(subset=['Event', 'Event_time']) #should not try to correct these

pheno_full = helpers.fillNA(pheno_full, index=pheno_full.index) #fast KNN
pheno_full.isnull().any()

Age                  False
BodyMassIndex        False
Smoking              False
BPTreatment          False
PrevalentDiabetes    False
PrevalentCHD         False
PrevalentHFAIL       False
Event                False
Event_time           False
SystolicBP           False
NonHDLcholesterol    False
Sex                  False
dtype: bool

In [25]:
pheno_full

Age  BodyMassIndex  Smoking  BPTreatment  \
Simulated_328   53.618         24.127      0.0            0   
Simulated_1644  36.811         27.992      0.0            0   
Simulated_1710  49.429         23.664      0.0            0   
Simulated_1732  48.842         26.804      0.0            0   
Simulated_1727  60.738         29.862      0.0            0   
...                ...            ...      ...          ...   
Simulated_1628  56.091         25.580      1.0            0   
Simulated_3424  46.889         22.762      0.0            0   
Simulated_2215  70.841         24.808      0.0            0   
Simulated_3426  25.920         20.520      0.0            0   
Simulated_1679  62.679         36.798      0.0            0   

                PrevalentDiabetes  PrevalentCHD  PrevalentHFAIL  Event  \
Simulated_328                 0.0           0.0             0.0    0.0   
Simulated_1644                0.0           0.0             0.0    0.0   
Simulated_1710                0.0           0.0             0.0    0.0   
Simulated_1732                0.0           0.0             0.0    0.0   
Simulated_1727                0.0           0.0             0.0    0.0   
...                           ...           ...             ...    ...   
Simulated_1628                0.0           0.0             1.0    0.0   
Simulated_3424                0.0           0.0             0.0    0.0   
Simulated_2215                0.0           0.0             0.0    0.0   
Simulated_3426                0.0           0.0             0.0    0.0   
Simulated_1679                0.0           0.0             0.0    0.0   

                Event_time  SystolicBP  NonHDLcholesterol  Sex  
Simulated_328       15.750     133.077              3.020    0  
Simulated_1644      15.881     108.914              5.480    0  
Simulated_1710      15.891     110.064              4.388    1  
Simulated_1732      15.918     128.059              5.119    0  
Simulated_1727      15.841     169.913              5.740    1  
...                    ...         ...                ...  ...  
Simulated_1628     -10.830     169.903              4.480    1  
Simulated_3424      15.940     122.995              3.669    0  
Simulated_2215       3.542     190.934              6.069    1  
Simulated_3426      15.901     117.032              2.789    1  
Simulated_1679      15.801     167.922              4.511    0  

[5424 rows x 12 columns]

In [24]:
reads_full.isnull().values.any()

False

In [7]:
#merge data and create features/labels

features = pd.merge(reads_full, pheno_full, left_index=True, right_index=True)
labels = features.pop('Event')
true_labels = labels.copy()
#labels.value_counts() # 0 - 4898, 1 - 445 --> highly imbalanced

X_train, X_test, y_train, y_test = helpers.split_and_scale_data(features, labels) #stratify here
#X_train, y_train = helpers.perform_SMOTE(X_train, y_train) #then also perform SMOTE

train_ids = X_train.index
test_ids = X_test.index

In [8]:
#remove metadata so we can perform dimensionality reduction on just the reads
metadata = [
            'Age', 
            'BodyMassIndex', 
            'BPTreatment', 
            'Smoking', 
            'PrevalentDiabetes', 
            'PrevalentHFAIL', 
            'Event_time', 
            'SystolicBP', 
            'NonHDLcholesterol', 
            'Sex'
           ]

meta_train = X_train[metadata].copy()
rds_train = X_train.drop(metadata, axis=1)

meta_test = X_test[metadata].copy()
rds_test = X_test.drop(metadata, axis=1)

In [9]:
PCA_train, PCA_test = models.run_PCA(rds_train, rds_test, n_components=50)

In [26]:
ET = meta_train.pop('Event_time')
LASSO_train, LASSO_test = models.run_LASSO(meta_train, meta_test, ET)

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV 1/5] END .....................alpha=0.0001;, score=-0.366 total time=   0.0s
[CV 2/5] END .....................alpha=0.0001;, score=-0.381 total time=   0.0s
[CV 3/5] END .....................alpha=0.0001;, score=-0.303 total time=   0.0s
[CV 4/5] END .....................alpha=0.0001;, score=-0.390 total time=   0.0s
[CV 5/5] END .....................alpha=0.0001;, score=-0.393 total time=   0.0s
[CV 1/5] END ......................alpha=0.001;, score=-0.366 total time=   0.0s
[CV 2/5] END ......................alpha=0.001;, score=-0.381 total time=   0.0s
[CV 3/5] END ......................alpha=0.001;, score=-0.303 total time=   0.0s
[CV 4/5] END ......................alpha=0.001;, score=-0.390 total time=   0.0s
[CV 5/5] END ......................alpha=0.001;, score=-0.393 total time=   0.0s
[CV 1/5] END .......................alpha=0.01;, score=-0.365 total time=   0.0s
[CV 2/5] END .......................alpha=0.01;, 

In [23]:
LASSO_train.columns

Index(['Age', 'Smoking', 'PrevalentDiabetes', 'PrevalentHFAIL', 'SystolicBP',
       'NonHDLcholesterol', 'Sex'],
      dtype='object')

In [51]:
UMAP_train, UMAP_test = models.run_UMAP(rds_train, rds_test)

In [10]:
AE_train, AE_test = models.run_AE(rds_train, rds_test)

Fitting 5 folds for each of 36 candidates, totalling 180 fits


2022-11-15 20:09:39.966561: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /sw/isaac/compilers/intel/oneAPI_2021.2.0/mpi/latest/libfabric/lib:/sw/isaac/compilers/intel/oneAPI_2021.2.0/mpi/latest/lib/release:/sw/isaac/compilers/intel/oneAPI_2021.2.0/mpi/latest/lib:/sw/isaac/compilers/intel/oneAPI_2021.2.0/ippcp/latest/lib/intel64:/sw/isaac/compilers/intel/oneAPI_2021.2.0/ipp/latest/lib/intel64:/sw/isaac/compilers/intel/oneAPI_2021.2.0/itac/latest/slib:/sw/isaac/compilers/intel/oneAPI_2021.2.0/mkl/latest/lib/intel64:/sw/isaac/compilers/intel/oneAPI_2021.2.0/compiler/latest/linux/lib:/sw/isaac/compilers/intel/oneAPI_2021.2.0/compiler/latest/linux/lib/x64:/sw/isaac/compilers/intel/oneAPI_2021.2.0/compiler/latest/linux/lib/emu:/sw/isaac/compilers/intel/oneAPI_2021.2.0/compiler/latest/linux/compiler/lib/intel64_lin:/sw/isaac/compil

51/51 [==============================] - 0s 2ms/step


In [10]:
#merge back together DR matrices and metadata

PCA_train_df = pd.DataFrame(PCA_train, index=train_ids).join(meta_train[['Age', 'Smoking', 'PrevalentDiabetes', 'PrevalentHFAIL', 'SystolicBP',
       'NonHDLcholesterol', 'Sex', 'Event_time']])
PCA_test_df = pd.DataFrame(PCA_test, index=test_ids).join(meta_test[['Age', 'Smoking', 'PrevalentDiabetes', 'PrevalentHFAIL', 'SystolicBP',
       'NonHDLcholesterol', 'Sex', 'Event_time']])

# LASSO_train_df = pd.DataFrame(LASSO_train, index=train_ids).join(meta_train)
# LASSO_test_df = pd.DataFrame(LASSO_test, index=test_ids).join(meta_test)

# UMAP_train_df = pd.DataFrame(UMAP_train, index=train_ids).join(meta_train)
# UMAP_test_df = pd.DataFrame(UMAP_test, index=test_ids).join(meta_test)

# AE_train_df = pd.DataFrame(AE_train)
# AE_test_df = pd.DataFrame(AE_test)

# AE_train_df = AE_train_df.set_index(train_ids)
# AE_test_df = AE_test_df.set_index(test_ids)

# AE_train_df = AE_train_df.join(meta_train[['Age', 'Smoking', 'PrevalentDiabetes', 'PrevalentHFAIL', 'SystolicBP',
#        'NonHDLcholesterol', 'Sex', 'Event_time']])
# AE_test_df = AE_test_df.join(meta_test[['Age', 'Smoking', 'PrevalentDiabetes', 'PrevalentHFAIL', 'SystolicBP',
#        'NonHDLcholesterol', 'Sex', 'Event_time']])

In [48]:
PCA_train_df

0          1         2          3         4         5  \
Simulated_2924  10.025265  13.324102  1.205117  -2.481085 -6.639184 -0.876260   
Simulated_6710  -0.572252   3.862004 -4.099744  -0.415420  1.889121 -3.970699   
Simulated_4536  -7.261539   2.798275 -3.572350   1.638795 -1.826676  0.049515   
Simulated_2912   4.602248  -0.410201  4.975525  14.673191 -4.120256  1.929673   
Simulated_5363   9.737341   2.778972  1.658529   1.371031 -1.487145  1.403374   
...                   ...        ...       ...        ...       ...       ...   
Simulated_6114  -2.086765   2.979667 -1.759668   1.502216 -4.280757  0.986041   
Simulated_534    0.810858  -5.178480 -4.203187   3.904067  1.214902  2.567415   
Simulated_4148 -12.319333   3.355203  1.502986   1.478671 -1.543760  0.195361   
Simulated_41    32.476666   7.509849 -4.583501   6.500684 -9.698954  0.007374   
Simulated_3371   4.281055   1.098266  0.709317   0.362665 -4.896680  1.641504   

                        6         7         8         9  ...       497  \
Simulated_2924   3.616534 -3.775468 -1.404810 -2.089013  ...  0.335454   
Simulated_6710  -1.239965 -0.357901 -2.278798  1.793296  ... -2.135600   
Simulated_4536   0.877689 -2.538451 -0.032343 -1.380018  ...  0.043410   
Simulated_2912 -11.655236  2.812299  3.458597  1.313667  ... -0.444034   
Simulated_5363   2.367802  1.069379  0.973029 -0.741879  ... -1.487070   
...                   ...       ...       ...       ...  ...       ...   
Simulated_6114   4.094157 -3.644820 -6.709914 -1.466124  ... -0.987991   
Simulated_534    2.771716  1.531209  1.120629 -2.687018  ... -1.637140   
Simulated_4148   0.252267 -2.980350  1.903589  0.366092  ...  0.397530   
Simulated_41     6.275538 -0.061005 -2.404849 -7.803659  ... -0.752320   
Simulated_3371   2.412267 -2.526964  0.377348 -1.476981  ... -0.662665   

                     498       499       Age   Smoking  PrevalentDiabetes  \
Simulated_2924  2.463316 -5.403702 -0.283613 -0.562030           3.801913   
Simulated_6710 -2.636289 -3.424612 -0.299635 -0.562030          -0.263025   
Simulated_4536 -1.552012 -0.428350  1.616029 -0.562030          -0.263025   
Simulated_2912 -1.099881  0.664101  1.332015 -0.562030          -0.263025   
Simulated_5363 -0.242765 -2.404791  1.672644 -0.562030          -0.263025   
...                  ...       ...       ...       ...                ...   
Simulated_6114  2.388337  0.445664 -1.117614  1.787616          -0.263025   
Simulated_534  -1.024990 -1.745535  0.930936 -0.562030          -0.263025   
Simulated_4148  0.090722  0.252949  0.224031 -0.562030          -0.263025   
Simulated_41   -2.975265  1.390035 -1.606409 -0.562030          -0.263025   
Simulated_3371  1.780413 -0.767920 -0.132148  1.787616          -0.263025   

                PrevalentHFAIL  SystolicBP  NonHDLcholesterol       Sex  
Simulated_2924       -0.157919   -0.132168           1.150605  1.121808  
Simulated_6710       -0.157919    1.804653          -0.536003 -0.891418  
Simulated_4536       -0.157919   -0.628687           1.450934 -0.891418  
Simulated_2912       -0.157919    0.993089           1.102991  1.121808  
Simulated_5363       -0.157919    3.744314           2.845453  1.121808  
...                        ...         ...                ...       ...  
Simulated_6114       -0.157919   -0.723413          -1.230973  1.121808  
Simulated_534         6.332369    2.391076          -0.481980 -0.891418  
Simulated_4148       -0.157919   -0.768071           0.727579 -0.891418  
Simulated_41         -0.157919   -0.995601          -1.039605 -0.891418  
Simulated_3371       -0.157919   -1.392754          -1.031364  1.121808  

[3740 rows x 507 columns]

In [60]:
df_AE.to_csv(PATH+'AE_reduced3.csv')

In [12]:
df_PCA.to_csv(PATH+'PCA_reduced2.csv')

In [ ]:
#run survival models

In [11]:
#change data to new format

# df_full = features
# df_full['Event'] = true_labels

df_PCA = pd.concat([PCA_train_df, PCA_test_df])
df_PCA['Event'] = true_labels

# df_LASSO = pd.concat([LASSO_train_df, LASSO_test_df])
# df_LASSO['Event'] = true_labels

# df_UMAP = pd.concat([UMAP_train_df, UMAP_test_df])
# df_UMAP['Event'] = true_labels

# df_AE = pd.concat([AE_train_df, AE_test_df])
# df_AE['Event'] = true_labels

In [55]:
#run baseline Cox Model with PCA
cph = survival_models.run_CoxPH(df_PCA)
#preds = cph.predict_survival_function(X)

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:1612: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently. Please see the following tips in the lifelines documentation: https://lifelines.readthedocs.io/en/latest/Examples.html#problems-with-convergence-in-the-cox-proportional-hazard-model
  "Newton-Rhaphson failed to converge sufficiently. {0}".format(CONVERGENCE_DOCS), exceptions.ConvergenceWarning


<lifelines.CoxPHFitter: fitted with 5343 total observations, 4898 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
      baseline estimation = breslow
   number of observations = 5343
number of events observed = 445
   partial log-likelihood = -1504.24
         time fit was run = 2022-11-11 18:35:51 UTC

---
                    coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
covariate                                                                                                                 
0                  -0.01       0.99       0.04            -0.09             0.06                 0.92                 1.06
1                  -0.01       0.99       0.13            -0.26             0.24                 0.77                 1.27
2                   0.02       1.02       0.09            -0.15             0.19                 0.86                 1.21
3                   0.03       1.03       0.08            -0.13             0.19                 0.87                 1.21
4                  -0.02       0.98       0.29            -0.59             0.56                 0.55                 1.75
5                   0.05       1.05       0.27            -0.48             0.58                 0.62                 1.78
6                   0.01       1.01       0.11            -0.20             0.22                 0.82                 1.24
7                  -0.06       0.94       0.12            -0.30             0.19                 0.74                 1.20
8                   0.02       1.02       0.16            -0.30             0.34                 0.74                 1.41
9                   0.01       1.01       0.16            -0.30             0.33                 0.74                 1.39
10                  0.07       1.07       0.16            -0.24             0.38                 0.79                 1.46
11                  0.03       1.03       0.20            -0.36             0.42                 0.70                 1.52
12                 -0.01       0.99       0.18            -0.35             0.34                 0.70                 1.40
13                 -0.01       0.99       0.21            -0.42             0.39                 0.66                 1.48
14                 -0.10       0.90       0.25            -0.59             0.38                 0.55                 1.47
15                 -0.00       1.00       0.13            -0.26             0.25                 0.77                 1.29
16                 -0.08       0.92       0.26            -0.59             0.42                 0.56                 1.53
17                 -0.04       0.96       0.24            -0.50             0.43                 0.60                 1.54
18                 -0.02       0.98       0.15            -0.31             0.26                 0.74                 1.30
19                  0.04       1.05       0.24            -0.42             0.51                 0.66                 1.67
20                 -0.04       0.96       0.15            -0.32             0.25                 0.72                 1.28
21                  0.01       1.01       0.17            -0.33             0.34                 0.72                 1.40
22                 -0.06       0.94       0.17            -0.39             0.27                 0.68                 1.31
23                  0.04       1.04       0.19            -0.34             0.41                 0.71                 1.51
24                  0.07       1.07       0.13            -0.19             0.32                 0.83                 1.37
25                  0.09       1.09       0.21            -0.32             0.50                 0.72                 1.65
26                  0.03       1.03       0.18            -0.33             0.39                 0.72                 1.47
27                  0.01       1.01       0.18            -0.35   

In [105]:
train = df_PCA.loc[train_ids]
test = df_PCA.loc[test_ids]
cph = survival_models.run_CoxPH(train)
preds = cph.predict_hazard(test)

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:1612: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently. Please see the following tips in the lifelines documentation: https://lifelines.readthedocs.io/en/latest/Examples.html#problems-with-convergence-in-the-cox-proportional-hazard-model
  "Newton-Rhaphson failed to converge sufficiently. {0}".format(CONVERGENCE_DOCS), exceptions.ConvergenceWarning


<lifelines.CoxPHFitter: fitted with 3740 total observations, 3429 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
      baseline estimation = breslow
   number of observations = 3740
number of events observed = 311
   partial log-likelihood = -1708.36
         time fit was run = 2022-11-11 23:21:06 UTC

---
                    coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
covariate                                                                                                                 
0                  -0.00       1.00       0.02            -0.04             0.04                 0.96                 1.04
1                  -0.01       0.99       0.04            -0.09             0.08                 0.92                 1.08
2                  -0.00       1.00       0.05            -0.10             0.10                 0.90                 1.10
3                   0.00       1.00       0.04            -0.07             0.08                 0.93                 1.08
4                  -0.00       1.00       0.08            -0.17             0.16                 0.85                 1.18
5                   0.01       1.01       0.08            -0.13             0.16                 0.88                 1.17
6                   0.00       1.00       0.05            -0.09             0.09                 0.91                 1.10
7                  -0.01       0.99       0.06            -0.12             0.10                 0.89                 1.11
8                   0.01       1.01       0.06            -0.10             0.12                 0.90                 1.13
9                   0.00       1.00       0.14            -0.26             0.27                 0.77                 1.30
10                  0.02       1.02       0.14            -0.25             0.28                 0.78                 1.32
11                  0.01       1.01       0.07            -0.13             0.15                 0.88                 1.16
12                  0.00       1.00       0.16            -0.30             0.31                 0.74                 1.36
13                 -0.00       1.00       0.16            -0.32             0.32                 0.73                 1.37
14                 -0.01       0.99       0.29            -0.58             0.56                 0.56                 1.75
15                 -0.01       0.99       0.05            -0.10             0.09                 0.90                 1.09
16                 -0.01       0.99       0.30            -0.60             0.59                 0.55                 1.80
17                 -0.01       0.99       0.05            -0.12             0.09                 0.89                 1.09
18                 -0.00       1.00       0.05            -0.10             0.09                 0.91                 1.09
19                  0.00       1.00       0.04            -0.08             0.08                 0.92                 1.08
20                  0.00       1.00       0.07            -0.13             0.14                 0.87                 1.15
21                 -0.02       0.98       0.06            -0.13             0.10                 0.87                 1.10
22                 -0.00       1.00       0.12            -0.23             0.23                 0.79                 1.25
23                  0.01       1.01       0.07            -0.12             0.14                 0.89                 1.15
24                  0.01       1.01       0.05            -0.10             0.11                 0.90                 1.12
25                 -0.00       1.00       0.16            -0.32             0.31                 0.73                 1.37
26                  0.01       1.01       0.07            -0.12             0.14                 0.89                 1.16
27                  0.00       1.00       0.11            -0.21   

AttributeError: CoxPHFitter has no attribute 'predict_hazard'

In [ ]:
concordance_index(test['Event_time'], preds)

In [91]:
#run baseline Cox Model with LASSO
cph = survival_models.run_CoxPH(df_LASSO)
#cph.predict_survival_function(X)

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:1612: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently. Please see the following tips in the lifelines documentation: https://lifelines.readthedocs.io/en/latest/Examples.html#problems-with-convergence-in-the-cox-proportional-hazard-model
  "Newton-Rhaphson failed to converge sufficiently. {0}".format(CONVERGENCE_DOCS), exceptions.ConvergenceWarning


<lifelines.CoxPHFitter: fitted with 5343 total observations, 4898 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
      baseline estimation = breslow
   number of observations = 5343
number of events observed = 445
   partial log-likelihood = -3356.71
         time fit was run = 2022-11-11 19:59:02 UTC

---
                    coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
covariate                                                                                                                 
Age                 0.32       1.38       0.06             0.20             0.44                 1.22                 1.55
BodyMassIndex      -0.01       0.99       0.05            -0.11             0.09                 0.90                 1.10
BPTreatment        -0.01       0.99       0.05            -0.10             0.09                 0.90                 1.09
Smoking            -0.01       0.99       0.05            -0.11             0.08                 0.90                 1.08
PrevalentDiabetes  -0.01       0.99       0.05            -0.10             0.09                 0.90                 1.10
PrevalentHFAIL      3.70      40.59       9.68           -15.26            22.67                 0.00             7.02e+09
SystolicBP          0.04       1.04       0.06            -0.07             0.15                 0.93                 1.16
NonHDLcholesterol  -0.02       0.98       0.05            -0.12             0.08                 0.88                 1.08
Sex                -0.00       1.00       0.05            -0.10             0.09                 0.91                 1.10

                    cmp to     z      p   -log2(p)
covariate                                         
Age                   0.00  5.22 <0.005      22.42
BodyMassIndex         0.00 -0.16   0.87       0.19
BPTreatment           0.00 -0.12   0.91       0.14
Smoking               0.00 -0.30   0.77       0.38
PrevalentDiabetes     0.00 -0.11   0.91       0.13
PrevalentHFAIL        0.00  0.38   0.70       0.51
SystolicBP            0.00  0.70   0.49       1.04
NonHDLcholesterol     0.00 -0.40   0.69       0.54
Sex                   0.00 -0.05   0.96       0.06
---
Concordance = 0.72
Partial AIC = 6731.42
log-likelihood ratio test = 228.61 on 9 df
-log2(p) of ll-ratio test = 144.47

In [57]:
#run baseline Cox Model with UMAP
cph = survival_models.run_CoxPH(df_UMAP)
#cph.predict_survival_function(X)

<lifelines.CoxPHFitter: fitted with 5343 total observations, 4898 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
      baseline estimation = breslow
   number of observations = 5343
number of events observed = 445
   partial log-likelihood = -3320.32
         time fit was run = 2022-11-11 19:06:24 UTC

---
                    coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
covariate                                                                                                                 
0                   0.03       1.03       0.03            -0.02             0.08                 0.98                 1.08
1                   0.14       1.15       0.03             0.08             0.19                 1.09                 1.21
Age                 0.65       1.91       0.06             0.52             0.77                 1.69                 2.17
BodyMassIndex      -0.03       0.97       0.05            -0.13             0.07                 0.88                 1.07
BPTreatment        -0.01       0.99       0.05            -0.11             0.08                 0.90                 1.08
Smoking            -0.04       0.97       0.05            -0.13             0.06                 0.87                 1.07
PrevalentDiabetes  -0.01       0.99       0.05            -0.11             0.08                 0.90                 1.09
PrevalentHFAIL      1.90       6.67       1.66            -1.35             5.14                 0.26               171.05
SystolicBP          0.07       1.07       0.05            -0.03             0.18                 0.97                 1.19
NonHDLcholesterol  -0.05       0.95       0.05            -0.15             0.05                 0.86                 1.06
Sex                 0.00       1.00       0.05            -0.09             0.10                 0.91                 1.10

                    cmp to     z      p   -log2(p)
covariate                                         
0                     0.00  1.17   0.24       2.04
1                     0.00  4.99 <0.005      20.69
Age                   0.00 10.16 <0.005      78.10
BodyMassIndex         0.00 -0.57   0.57       0.81
BPTreatment           0.00 -0.31   0.76       0.40
Smoking               0.00 -0.70   0.48       1.05
PrevalentDiabetes     0.00 -0.22   0.83       0.28
PrevalentHFAIL        0.00  1.15   0.25       1.99
SystolicBP            0.00  1.32   0.19       2.42
NonHDLcholesterol     0.00 -0.91   0.36       1.47
Sex                   0.00  0.02   0.99       0.02
---
Concordance = 0.73
Partial AIC = 6662.63
log-likelihood ratio test = 301.40 on 11 df
-log2(p) of ll-ratio test = 190.52

In [92]:
#run baseline Cox Model with AE
cph = survival_models.run_CoxPH(df_AE)
#cph.predict_survival_function(X)

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:1612: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently. Please see the following tips in the lifelines documentation: https://lifelines.readthedocs.io/en/latest/Examples.html#problems-with-convergence-in-the-cox-proportional-hazard-model
  "Newton-Rhaphson failed to converge sufficiently. {0}".format(CONVERGENCE_DOCS), exceptions.ConvergenceWarning


<lifelines.CoxPHFitter: fitted with 5343 total observations, 4898 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
      baseline estimation = breslow
   number of observations = 5343
number of events observed = 445
   partial log-likelihood = -3323.32
         time fit was run = 2022-11-11 19:59:02 UTC

---
                    coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
covariate                                                                                                                 
0                   0.06       1.06       0.20            -0.34             0.45                 0.71                 1.56
1                   0.03       1.03       0.20            -0.35             0.41                 0.70                 1.51
2                  -0.07       0.93       0.20            -0.46             0.33                 0.63                 1.39
3                   0.08       1.09       0.20            -0.30             0.47                 0.74                 1.59
4                   0.11       1.11       0.20            -0.28             0.50                 0.76                 1.64
5                  -0.06       0.95       0.20            -0.45             0.34                 0.64                 1.40
6                   0.07       1.08       0.20            -0.32             0.47                 0.73                 1.59
7                   0.01       1.01       0.20            -0.39             0.41                 0.68                 1.50
8                  -0.07       0.93       0.20            -0.47             0.33                 0.62                 1.39
9                   0.17       1.18       0.20            -0.23             0.57                 0.79                 1.76
10                  0.13       1.13       0.20            -0.28             0.53                 0.76                 1.69
11                 -0.01       0.99       0.20            -0.41             0.39                 0.67                 1.47
12                  0.04       1.04       0.20            -0.35             0.43                 0.70                 1.54
13                  0.11       1.11       0.20            -0.29             0.50                 0.75                 1.65
14                  0.02       1.03       0.20            -0.37             0.42                 0.69                 1.52
15                  0.09       1.09       0.20            -0.30             0.48                 0.74                 1.62
16                  0.20       1.22       0.20            -0.19             0.59                 0.83                 1.81
17                 -0.07       0.94       0.20            -0.46             0.33                 0.63                 1.39
18                  0.08       1.08       0.20            -0.31             0.47                 0.73                 1.59
19                 -0.09       0.91       0.20            -0.49             0.31                 0.61                 1.36
20                 -0.04       0.96       0.20            -0.44             0.36                 0.65                 1.44
21                  0.12       1.13       0.21            -0.28             0.52                 0.76                 1.69
22                  0.03       1.03       0.20            -0.35             0.42                 0.70                 1.53
23                 -0.00       1.00       0.20            -0.39             0.39                 0.68                 1.47
24                  0.02       1.02       0.20            -0.38             0.41                 0.68                 1.51
25                 -0.03       0.97       0.20            -0.42             0.36                 0.65                 1.44
26                 -0.13       0.88       0.20            -0.52             0.27                 0.59                 1.31
27                 -0.07       0.94       0.20            -0.46   

In [110]:
#fix data for AFT models

df_PCA = df_PCA[df_PCA['Event_time'] > 0]
df_LASSO = df_LASSO[df_LASSO['Event_time'] > 0]
df_UMAP = df_UMAP[df_UMAP['Event_time'] > 0]
df_AE = df_AE[df_AE['Event_time'] > 0]

In [96]:
#run baseline AFT with AE
aft = survival_models.run_WeibullAFT(df_AE)
#aft.predict_survival_function(X)

<lifelines.WeibullAFTFitter: fitted with 4395 total observations, 4080 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
   number of observations = 4395
number of events observed = 315
           log-likelihood = -147.92
         time fit was run = 2022-11-11 20:23:38 UTC

---
                            coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
param   covariate                                                                                                                 
lambda_ 0                   0.01       1.01       0.02            -0.02             0.04                 0.98                 1.04
        1                   0.00       1.00       0.01            -0.03             0.03                 0.97                 1.03
        2                  -0.00       1.00       0.02            -0.03             0.03                 0.97                 1.03
        3                  -0.02       0.98       0.01            -0.04             0.01                 0.96                 1.01
        4                  -0.02       0.98       0.01            -0.04             0.01                 0.96                 1.01
        5                   0.02       1.02       0.02            -0.01             0.05                 0.99                 1.05
        6                  -0.00       1.00       0.01            -0.03             0.03                 0.97                 1.03
        7                  -0.01       0.99       0.02            -0.04             0.02                 0.96                 1.02
        8                  -0.00       1.00       0.02            -0.03             0.03                 0.97                 1.03
        9                  -0.03       0.97       0.02            -0.06             0.00                 0.94                 1.00
        10                 -0.02       0.98       0.02            -0.05             0.01                 0.95                 1.01
        11                  0.01       1.01       0.02            -0.02             0.04                 0.98                 1.04
        12                  0.01       1.01       0.02            -0.02             0.04                 0.98                 1.04
        13                 -0.02       0.98       0.02            -0.05             0.01                 0.95                 1.01
        14                 -0.00       1.00       0.02            -0.03             0.03                 0.97                 1.03
        15                 -0.01       0.99       0.02            -0.04             0.02                 0.96                 1.02
        16                 -0.02       0.98       0.02            -0.05             0.01                 0.95                 1.01
        17                 -0.00       1.00       0.02            -0.03             0.03                 0.97                 1.03
        18                 -0.01       0.99       0.02            -0.04             0.02                 0.96                 1.02
        19                  0.02       1.02       0.02            -0.01             0.05                 0.99                 1.05
        20                  0.00       1.00       0.02            -0.03             0.03                 0.97                 1.03
        21                 -0.01       0.99       0.02            -0.04             0.02                 0.96                 1.02
        22                  0.00       1.00       0.01            -0.02             0.03                 0.98                 1.03
        23                 -0.01       0.99       0.01            -0.04             0.02                 0.96                 1.02
        24                  0.01       1.01       0.02            -0.02             0.04                 0.98                 1.04
        25                  0.01       1.01       0.02            -0.02             0.04                 0.98                 1.

In [113]:
#run baseline AFT with PCA
train = df_PCA.loc[train_ids]
test = df_PCA.loc[test_ids]

train = train[train['Event_time'] > 0]
test = test[test['Event_time'] > 0]

aft = survival_models.run_WeibullAFT(train)
preds = aft.predict_expectation(test)
concordance_index(test['Event_time'], preds)

<lifelines.WeibullAFTFitter: fitted with 3088 total observations, 2863 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
   number of observations = 3088
number of events observed = 225
           log-likelihood = 148.75
         time fit was run = 2022-11-11 23:52:16 UTC

---
                            coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
param   covariate                                                                                                                 
lambda_ 0                   0.01       1.01       0.00             0.01             0.01                 1.01                 1.01
        1                  -0.00       1.00       0.00            -0.01             0.00                 0.99                 1.00
        2                  -0.00       1.00       0.00            -0.01             0.00                 0.99                 1.00
        3                   0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        4                  -0.00       1.00       0.01            -0.02             0.01                 0.98                 1.01
        5                  -0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        6                  -0.00       1.00       0.00            -0.01             0.00                 0.99                 1.00
        7                   0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        8                  -0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        9                   0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        10                 -0.01       0.99       0.00            -0.01             0.00                 0.99                 1.00
        11                  0.00       1.00       0.01            -0.01             0.02                 0.99                 1.02
        12                 -0.00       1.00       0.01            -0.02             0.01                 0.98                 1.01
        13                  0.01       1.01       0.01            -0.00             0.02                 1.00                 1.02
        14                  0.01       1.01       0.01            -0.01             0.02                 0.99                 1.02
        15                 -0.01       0.99       0.01            -0.02             0.01                 0.98                 1.01
        16                  0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        17                  0.00       1.00       0.01            -0.01             0.02                 0.99                 1.02
        18                  0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        19                  0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        20                  0.01       1.01       0.01             0.00             0.03                 1.00                 1.03
        21                  0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        22                 -0.00       1.00       0.01            -0.02             0.01                 0.98                 1.01
        23                  0.01       1.01       0.01            -0.01             0.02                 0.99                 1.02
        24                  0.00       1.00       0.01            -0.01             0.01                 0.99                 1.01
        25                 -0.01       0.99       0.01            -0.02             0.00                 0.98                 1.0

0.5375238221578936

In [98]:
#run baseline AFT with LASSO
aft = survival_models.run_WeibullAFT(df_LASSO)
#aft.predict_survival_function(X)

<lifelines.WeibullAFTFitter: fitted with 4395 total observations, 4080 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
   number of observations = 4395
number of events observed = 315
           log-likelihood = -202.10
         time fit was run = 2022-11-11 23:00:10 UTC

---
                            coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
param   covariate                                                                                                                 
lambda_ Age                -0.03       0.97       0.00            -0.04            -0.02                 0.96                 0.98
        BPTreatment         0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        BodyMassIndex       0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        NonHDLcholesterol   0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        PrevalentDiabetes   0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        PrevalentHFAIL    -21.77       0.00       3.92           -29.45           -14.09                 0.00                 0.00
        Sex                -0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        Smoking             0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        SystolicBP         -0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        Intercept          -4.27       0.01       0.62            -5.49            -3.06                 0.00                 0.05
rho_    Intercept           2.74      15.51       0.05             2.64             2.84                14.02                17.14

                            cmp to     z      p   -log2(p)
param   covariate                                         
lambda_ Age                   0.00 -6.43 <0.005      32.84
        BPTreatment           0.00  0.75   0.45       1.14
        BodyMassIndex         0.00  0.27   0.79       0.35
        NonHDLcholesterol     0.00  0.76   0.45       1.16
        PrevalentDiabetes     0.00  0.34   0.73       0.45
        PrevalentHFAIL        0.00 -5.56 <0.005      25.11
        Sex                   0.00 -0.05   0.96       0.06
        Smoking               0.00  0.89   0.38       1.41
        SystolicBP            0.00 -0.64   0.52       0.95
        Intercept             0.00 -6.88 <0.005      37.29
rho_    Intercept             0.00 53.46 <0.005        inf
---
Concordance = 0.73
AIC = 426.21
log-likelihood ratio test = 102.79 on 9 df
-log2(p) of ll-ratio test = 57.69

In [99]:
#run baseline AFT with UMAP
aft = survival_models.run_WeibullAFT(df_UMAP)
#aft.predict_survival_function(X)

<lifelines.WeibullAFTFitter: fitted with 4395 total observations, 4080 right-censored observations>
             duration col = 'Event_time'
                event col = 'Event'
   number of observations = 4395
number of events observed = 315
           log-likelihood = -201.99
         time fit was run = 2022-11-11 23:00:15 UTC

---
                            coef  exp(coef)   se(coef)   coef lower 95%   coef upper 95%  exp(coef) lower 95%  exp(coef) upper 95%
param   covariate                                                                                                                 
lambda_ 0                   0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        1                   0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        Age                -0.03       0.97       0.00            -0.04            -0.02                 0.96                 0.98
        BPTreatment         0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        BodyMassIndex       0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        NonHDLcholesterol   0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        PrevalentDiabetes   0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        PrevalentHFAIL    -22.75       0.00       7.21           -36.88            -8.62                 0.00                 0.00
        Sex                -0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        Smoking             0.00       1.00       0.00            -0.00             0.01                 1.00                 1.01
        SystolicBP         -0.00       1.00       0.00            -0.01             0.01                 0.99                 1.01
        Intercept          -4.43       0.01       1.16            -6.71            -2.15                 0.00                 0.12
rho_    Intercept           2.74      15.51       0.05             2.64             2.84                14.02                17.15

                            cmp to     z      p   -log2(p)
param   covariate                                         
lambda_ 0                     0.00  0.47   0.64       0.64
        1                     0.00  0.02   0.98       0.03
        Age                   0.00 -6.43 <0.005      32.90
        BPTreatment           0.00  0.74   0.46       1.13
        BodyMassIndex         0.00  0.26   0.79       0.33
        NonHDLcholesterol     0.00  0.76   0.45       1.17
        PrevalentDiabetes     0.00  0.33   0.74       0.43
        PrevalentHFAIL        0.00 -3.16 <0.005       9.29
        Sex                   0.00 -0.05   0.96       0.06
        Smoking               0.00  0.88   0.38       1.40
        SystolicBP            0.00 -0.63   0.53       0.92
        Intercept             0.00 -3.81 <0.005      12.84
rho_    Intercept             0.00 53.46 <0.005        inf
---
Concordance = 0.73
AIC = 429.98
log-likelihood ratio test = 103.01 on 11 df
-log2(p) of ll-ratio test = 54.30

In [23]:
import importlib
importlib.reload(survival_models)

<module 'survival_models' from '/nfs/home/ababjac/dream-finrisk/scripts/survival_models.py'>

In [3]:
#again change data format
df_PCA = pd.read_csv(PATH+'PCA_reduced2.csv', header=0, index_col=0)
features = df_PCA.copy()
times = features.pop('Event_time')
events = features.pop('Event')
labels = helpers.make_structured_array(events, times)
X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.2, random_state=5)

In [24]:
cindex, enc_grid = survival_models.run_ElasticNetCox(X_train.values, X_test.values, y_train, y_test)
print('Concordance:', cindex)

/nfs/home/ababjac/dream-finrisk/scripts/survival_models.py:71: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  cox_elastic_net.fit(X_train, y_train)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


Fitting 5 folds for each of 400 candidates, totalling 2000 fits
[CV 1/5] END alphas=[0.11610733829176087], l1_ratio=0.001;, score=0.617 total time=   0.1s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


[CV 2/5] END alphas=[0.11610733829176087], l1_ratio=0.001;, score=0.613 total time=   0.1s
[CV 3/5] END alphas=[0.11610733829176087], l1_ratio=0.001;, score=0.545 total time=   0.1s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


...

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


[CV 5/5] END alphas=[0.0011610733829176142], l1_ratio=0.1;, score=0.711 total time=   0.1s
[CV 1/5] END alphas=[0.0011610733829176142], l1_ratio=1;, score=0.656 total time=   0.1s
[CV 2/5] END alphas=[0.0011610733829176142], l1_ratio=1;, score=0.646 total time=   0.1s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:372: FitFailedWarning: 
2 fits failed out of a total of 2000.
The score on these train-test partitions f

[CV 3/5] END alphas=[0.0011610733829176142], l1_ratio=1;, score=0.725 total time=   0.1s
[CV 4/5] END alphas=[0.0011610733829176142], l1_ratio=1;, score=0.669 total time=   0.1s
[CV 5/5] END alphas=[0.0011610733829176142], l1_ratio=1;, score=0.690 total time=   0.1s
Concordance: 0.691961963419963


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_search.py:972: UserWarning: One or more of the test scores are non-finite: [0.62351262 0.65245605 0.69458223 0.5        0.62273839 0.65286204
 0.69456711 0.5        0.61838821 0.65268522 0.69523028 0.5
 0.62018827 0.65201585 0.6956593  0.50025061 0.62050419 0.65307223
 0.69588153 0.50025061 0.6202181  0.67158738 0.69655622 0.50025061
 0.61919957 0.67011491 0.69748375 0.50025061 0.61798373 0.66942043
 0.69834732 0.50025061 0.65494206 0.6686839  0.69919521 0.49467257
 0.65513559 0.66798364 0.69988153 0.49467257 0.65445513 0.66601611
 0.70073566 0.48529211 0.65283259 0.66102703 0.70133646 0.48529451
 0.65031823 0.63596006 0.70167853 0.48529451 0.64168909 0.62570753
 0.70227458 0.48529451 0.63875549 0.62309035 0.70259281 0.48529451
 0.63677336 0.62173461 0.70287936 0.48529451 0.63590389 0.64476309
 0.70306735 0.55425798 0.6329951  0.63785676 0.70346815 0.58018738
 0.64006243 0.61778677 0.70346772 0.64154334 0.

In [34]:
enc_grid.best_params_

{'alphas': [0.008989769533208247], 'l1_ratio': 1}

In [21]:
cindex, rf_grid = survival_models.run_RandomSurvival(X_train.values, X_test.values, y_train, y_test)
print('Concordance:', cindex)

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV 1/5] END ....max_depth=6, max_features=sqrt;, score=0.645 total time=47.6min
[CV 2/5] END ....max_depth=6, max_features=sqrt;, score=0.653 total time=52.2min
[CV 3/5] END ....max_depth=6, max_features=sqrt;, score=0.731 total time=55.8min
[CV 4/5] END ....max_depth=6, max_features=sqrt;, score=0.667 total time=54.9min
[CV 5/5] END ....max_depth=6, max_features=sqrt;, score=0.737 total time=48.7min
[CV 1/5] END ....max_depth=6, max_features=log2;, score=0.631 total time=33.7min
[CV 2/5] END ....max_depth=6, max_features=log2;, score=0.649 total time=37.1min
[CV 3/5] END ....max_depth=6, max_features=log2;, score=0.721 total time=39.4min
[CV 4/5] END ....max_depth=6, max_features=log2;, score=0.667 total time=38.7min
[CV 5/5] END ....max_depth=6, max_features=log2;, score=0.721 total time=34.1min
[CV 1/5] END ....max_depth=7, max_features=sqrt;, score=0.642 total time=49.8min
[CV 2/5] END ....max_depth=7, max_features=sqrt;,

KeyboardInterrupt: 

In [ ]:
rf_grid.best_params_

In [22]:
cindex, gbs_grid = survival_models.run_SurvivalGB(X_train.values, X_test.values, y_train, y_test)
print('Concordance:', cindex)

Fitting 5 folds for each of 18 candidates, totalling 90 fits
[CV 1/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.610 total time= 1.2min
[CV 2/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.681 total time= 1.2min
[CV 3/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.732 total time= 1.2min
[CV 4/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.684 total time= 1.2min
[CV 5/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.689 total time= 1.2min
[CV 1/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.608 total time= 1.2min
[CV 2/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.663 total time= 1.2min
[CV 3/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.737 total time= 1.2min
[CV 4/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.693 total time= 1.2min
[CV 5/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.688 total time= 1.2min
[CV 1/5] END loss=coxph, max_depth=6, max_feature

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base

Concordance: 0.6690110073035227


In [23]:
print(cindex)
gbs_grid.best_params_

0.6690110073035227


{'loss': 'coxph', 'max_depth': 5, 'max_features': 'sqrt'}

In [20]:
cindex, ssvm_grid = survival_models.run_SurvivalSVM(X_train.values, X_test.values, y_train, y_test)
print('Concordance:', cindex)

Fitting 5 folds for each of 36 candidates, totalling 180 fits
[CV 1/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.439 total time=   0.4s
[CV 2/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.501 total time=   0.3s
[CV 3/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.453 total time=   0.3s
[CV 4/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.473 total time=   0.3s
[CV 5/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.495 total time=   0.3s
[CV 1/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.507 total time=   1.5s
[CV 2/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.519 total time=   1.5s
[CV 3/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.487 total time=   1.4s
[CV 4/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.523 total time=   1.4s
[CV 5/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.501 total time=   1.4s
[CV 1/5] END alpha=0.01, gamma=1, kernel=sigmoid;, score=0.462 total time=   1.9s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 2/5] END alpha=0.01, gamma=1, kernel=sigmoid;, score=0.490 total time=   6.5s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 3/5] END alpha=0.01, gamma=1, kernel=sigmoid;, score=0.509 total time=   6.8s


...

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 5/5] END alpha=10, gamma=0.1, kernel=sigmoid;, score=0.571 total time=  13.0s
[CV 1/5] END alpha=10, gamma=0.01, kernel=linear;, score=0.439 total time=   0.4s
[CV 2/5] END alpha=10, gamma=0.01, kernel=linear;, score=0.501 total time=   0.3s
[CV 3/5] END alpha=10, gamma=0.01, kernel=linear;, score=0.453 total time=   0.3s
[CV 4/5] END alpha=10, gamma=0.01, kernel=linear;, score=0.473 total time=   0.3s
[CV 5/5] END alpha=10, gamma=0.01, kernel=linear;, score=0.495 total time=   0.3s
[CV 1/5] END ..alpha=10, gamma=0.01, kernel=rbf;, score=0.542 total time=   4.6s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 2/5] END ..alpha=10, gamma=0.01, kernel=rbf;, score=0.597 total time=   8.3s
[CV 3/5] END ..alpha=10, gamma=0.01, kernel=rbf;, score=0.623 total time=   5.6s
[CV 4/5] END ..alpha=10, gamma=0.01, kernel=rbf;, score=0.614 total time=   9.4s
[CV 5/5] END ..alpha=10, gamma=0.01, kernel=rbf;, score=0.531 total time=   8.6s
[CV 1/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.556 total time=   7.0s
[CV 2/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.603 total time=   3.4s
[CV 3/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.683 total time=   1.7s
[CV 4/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.586 total time=   4.5s
[CV 5/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.581 total time=   5.2s
Concordance: 0.5766245656380699


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_search.py:926: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  self.best_estimator_.fit(X, y, **fit_params)


In [25]:
ssvm_grid.best_params_

{'alpha': 0.01, 'gamma': 0.01, 'kernel': 'rbf'}

In [26]:
#again change data format
df_AE = pd.read_csv(PATH+'AE_reduced.csv', header=0, index_col=0)
features = df_AE.copy()
times = features.pop('Event_time')
events = features.pop('Event')
labels = helpers.make_structured_array(events, times)
X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.2, random_state=5)

In [27]:
cindex, enc_grid2 = survival_models.run_ElasticNetCox(X_train.values, X_test.values, y_train, y_test)

/nfs/home/ababjac/dream-finrisk/scripts/survival_models.py:71: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  cox_elastic_net.fit(X_train, y_train)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are

Fitting 5 folds for each of 400 candidates, totalling 2000 fits
[CV 1/5] END alphas=[0.10827296509906786], l1_ratio=0.001;, score=0.666 total time=   0.0s
[CV 2/5] END alphas=[0.10827296509906786], l1_ratio=0.001;, score=0.675 total time=   0.0s
[CV 3/5] END alphas=[0.10827296509906786], l1_ratio=0.001;, score=0.772 total time=   0.0s
[CV 4/5] END alphas=[0.10827296509906786], l1_ratio=0.001;, score=0.683 total time=   0.0s
[CV 5/5] END alphas=[0.10827296509906786], l1_ratio=0.001;, score=0.734 total time=   0.0s
[CV 1/5] END alphas=[0.10827296509906786], l1_ratio=0.01;, score=0.667 total time=   0.0s
[CV 2/5] END alphas=[0.10827296509906786], l1_ratio=0.01;, score=0.680 total time=   0.0s
[CV 3/5] END alphas=[0.10827296509906786], l1_ratio=0.01;, score=0.775 total time=   0.0s
[CV 4/5] END alphas=[0.10827296509906786], l1_ratio=0.01;, score=0.682 total time=   0.0s
[CV 5/5] END alphas=[0.10827296509906786], l1_ratio=0.01;, score=0.735 total time=   0.0s
[CV 1/5] END alphas=[0.10827296

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, 

[CV 5/5] END alphas=[0.10827296509906786], l1_ratio=1;, score=0.500 total time=   0.0s
[CV 1/5] END alphas=[0.10335179173351586], l1_ratio=0.001;, score=0.667 total time=   0.0s
[CV 2/5] END alphas=[0.10335179173351586], l1_ratio=0.001;, score=0.676 total time=   0.0s
[CV 3/5] END alphas=[0.10335179173351586], l1_ratio=0.001;, score=0.772 total time=   0.0s
[CV 4/5] END alphas=[0.10335179173351586], l1_ratio=0.001;, score=0.683 total time=   0.0s
[CV 5/5] END alphas=[0.10335179173351586], l1_ratio=0.001;, score=0.734 total time=   0.0s
[CV 1/5] END alphas=[0.10335179173351586], l1_ratio=0.01;, score=0.667 total time=   0.0s
[CV 2/5] END alphas=[0.10335179173351586], l1_ratio=0.01;, score=0.680 total time=   0.0s
[CV 3/5] END alphas=[0.10335179173351586], l1_ratio=0.01;, score=0.775 total time=   0.0s
[CV 4/5] END alphas=[0.10335179173351586], l1_ratio=0.01;, score=0.682 total time=   0.0s
[CV 5/5] END alphas=[0.10335179173351586], l1_ratio=0.01;, score=0.736 total time=   0.0s
[CV 1/5]

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, consider decreasing alpha.
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: UserWarning: all coefficients are zero, 

...

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


[CV 3/5] END alphas=[0.0011882944553250026], l1_ratio=1;, score=0.730 total time=   0.0s
[CV 4/5] END alphas=[0.0011882944553250026], l1_ratio=1;, score=0.658 total time=   0.0s
[CV 5/5] END alphas=[0.0011882944553250026], l1_ratio=1;, score=0.749 total time=   0.0s
[CV 1/5] END alphas=[0.001134284638390296], l1_ratio=0.001;, score=0.647 total time=   0.1s
[CV 2/5] END alphas=[0.001134284638390296], l1_ratio=0.001;, score=0.634 total time=   0.1s
[CV 3/5] END alphas=[0.001134284638390296], l1_ratio=0.001;, score=0.695 total time=   0.1s
[CV 4/5] END alphas=[0.001134284638390296], l1_ratio=0.001;, score=0.639 total time=   0.2s
[CV 5/5] END alphas=[0.001134284638390296], l1_ratio=0.001;, score=0.720 total time=   0.1s
[CV 1/5] END alphas=[0.001134284638390296], l1_ratio=0.01;, score=0.647 total time=   0.1s
[CV 2/5] END alphas=[0.001134284638390296], l1_ratio=0.01;, score=0.634 total time=   0.1s
[CV 3/5] END alphas=[0.001134284638390296], l1_ratio=0.01;, score=0.695 total time=   0.1s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


[CV 1/5] END alphas=[0.0010827296509906836], l1_ratio=0.001;, score=0.647 total time=   0.1s
[CV 2/5] END alphas=[0.0010827296509906836], l1_ratio=0.001;, score=0.633 total time=   0.1s
[CV 3/5] END alphas=[0.0010827296509906836], l1_ratio=0.001;, score=0.694 total time=   0.2s
[CV 4/5] END alphas=[0.0010827296509906836], l1_ratio=0.001;, score=0.638 total time=   0.2s
[CV 5/5] END alphas=[0.0010827296509906836], l1_ratio=0.001;, score=0.720 total time=   0.1s
[CV 1/5] END alphas=[0.0010827296509906836], l1_ratio=0.01;, score=0.647 total time=   0.1s
[CV 2/5] END alphas=[0.0010827296509906836], l1_ratio=0.01;, score=0.633 total time=   0.1s
[CV 3/5] END alphas=[0.0010827296509906836], l1_ratio=0.01;, score=0.695 total time=   0.2s
[CV 4/5] END alphas=[0.0010827296509906836], l1_ratio=0.01;, score=0.638 total time=   0.2s
[CV 5/5] END alphas=[0.0010827296509906836], l1_ratio=0.01;, score=0.720 total time=   0.1s
[CV 1/5] END alphas=[0.0010827296509906836], l1_ratio=0.1;, score=0.650 tot

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization terminated early, you might want to increase the number of iterations (max_iter=500).
  estimator.fit(X_train, y_train, **fit_params)


In [28]:
print('Concordance:', cindex)
enc_grid2.best_params_

Concordance: 0.6973719802742462


{'alphas': [0.008383182469240965], 'l1_ratio': 1}

In [33]:
cindex, rf_grid2 = survival_models.run_RandomSurvival(X_train.values, X_test.values, y_train, y_test)

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV 1/5] END ....max_depth=6, max_features=sqrt;, score=0.664 total time=75.2min
[CV 2/5] END ....max_depth=6, max_features=sqrt;, score=0.635 total time=85.7min


KeyboardInterrupt: 

In [ ]:
print('Concordance:', cindex)
rf_grid2.best_params_

In [29]:
cindex, gbs_grid2 = survival_models.run_SurvivalGB(X_train.values, X_test.values, y_train, y_test)

Fitting 5 folds for each of 18 candidates, totalling 90 fits
[CV 1/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.663 total time= 1.2min
[CV 2/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.635 total time= 1.2min
[CV 3/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.707 total time= 1.2min
[CV 4/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.696 total time= 1.2min
[CV 5/5] END loss=coxph, max_depth=5, max_features=sqrt;, score=0.678 total time= 1.2min
[CV 1/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.657 total time= 1.1min
[CV 2/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.625 total time= 1.1min
[CV 3/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.694 total time= 1.1min
[CV 4/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.692 total time= 1.2min
[CV 5/5] END loss=coxph, max_depth=5, max_features=log2;, score=0.669 total time= 1.2min
[CV 1/5] END loss=coxph, max_depth=6, max_feature

/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sksurv/ensemble/boosting.py:955: RuntimeWarning: invalid value encountered in log
  time = numpy.log(time)
/nfs/home/ababjac/base

Concordance: 0.6174285773736449


In [30]:
print('Concordance:', cindex)
gbs_grid2.best_params_

Concordance: 0.6174285773736449


{'loss': 'coxph', 'max_depth': 5, 'max_features': 'sqrt'}

In [31]:
cindex, ssvm_grid2 = survival_models.run_SurvivalSVM(X_train.values, X_test.values, y_train, y_test)

Fitting 5 folds for each of 36 candidates, totalling 180 fits
[CV 1/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.657 total time=   0.7s
[CV 2/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.613 total time=   1.3s
[CV 3/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.710 total time=   1.0s
[CV 4/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.651 total time=   1.1s
[CV 5/5] END alpha=0.01, gamma=1, kernel=linear;, score=0.731 total time=   1.0s
[CV 1/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.573 total time=   1.3s
[CV 2/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.565 total time=   1.3s
[CV 3/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.612 total time=   1.3s
[CV 4/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.555 total time=   1.4s
[CV 5/5] END ...alpha=0.01, gamma=1, kernel=rbf;, score=0.591 total time=   1.3s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 1/5] END alpha=0.01, gamma=1, kernel=sigmoid;, score=0.499 total time=   2.5s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 2/5] END alpha=0.01, gamma=1, kernel=sigmoid;, score=0.500 total time=   1.6s


...

[CV 3/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.607 total time=  23.0s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 4/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.625 total time=  21.0s


/nfs/home/ababjac/base-venv/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:680: ConvergenceWarning: Optimization did not converge: Warning: Maximum number of iterations has been exceeded.
  estimator.fit(X_train, y_train, **fit_params)


[CV 5/5] END alpha=10, gamma=0.01, kernel=sigmoid;, score=0.639 total time=  20.7s


In [32]:
print('Concordance:', cindex)
ssvm_grid2.best_params_

Concordance: 0.6389021827337231


{'alpha': 0.01, 'gamma': 1, 'kernel': 'linear'}